<a href="https://colab.research.google.com/github/seunghyeokkim/ByeolDaJul/blob/main/TF_IDF%2CLSTM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [6]:
!pip install datasets
!wget https://raw.githubusercontent.com/warnikchow/sae4k/master/data/sae4k_v2.txt #데이터셋 다운로드


--2024-03-15 04:49:21--  https://raw.githubusercontent.com/warnikchow/sae4k/master/data/sae4k_v2.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.110.133, 185.199.108.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.110.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4756575 (4.5M) [text/plain]
Saving to: ‘sae4k_v2.txt’

sae4k_v2.txt        100%[===================>]   4.54M  --.-KB/s    in 0.07s   

2024-03-15 04:49:21 (60.9 MB/s) - ‘sae4k_v2.txt’ saved [4756575/4756575]



데이터 설명용 코드

In [2]:
# # coding=utf-8
# Copyright 2020 The HuggingFace Datasets Authors and the current dataset script contributor.
#
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
#     http://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.
# """Structured Argument Extraction for Korean"""


# import csv
# import datasets


# _CITATION = """\
# @article{cho2019machines,
#   title={Machines Getting with the Program: Understanding Intent Arguments of Non-Canonical Directives},
#   author={Cho, Won Ik and Moon, Young Ki and Moon, Sangwhan and Kim, Seok Min and Kim, Nam Soo},
#   journal={arXiv preprint arXiv:1912.00342},
#   year={2019}
# }
# """

# _DESCRIPTION = """\
# This new dataset is designed to extract intent from non-canonical directives which will help dialog managers
# extract intent from user dialog that may have no clear objective or are paraphrased forms of utterances.
# """

# _HOMEPAGE = "https://github.com/warnikchow/sae4k"

# _LICENSE = "CC-BY-SA-4.0"

# _TRAIN_DOWNLOAD_URL = "https://raw.githubusercontent.com/warnikchow/sae4k/master/data/sae4k_v1.txt"


In [7]:
class KorSae(datasets.GeneratorBasedBuilder):
    """Structured Argument Extraction for Korean"""

    VERSION = datasets.Version("1.1.0")

    def _info(self):

        return datasets.DatasetInfo(
            description=_DESCRIPTION,
            features=datasets.Features(
                {
                    "intent_pair1": datasets.Value("string"),
                    "intent_pair2": datasets.Value("string"),
                    "label": datasets.features.ClassLabel(
                        names=[
                            "yes/no",
                            "alternative",
                            "wh- questions",
                            "prohibitions",
                            "requirements",
                            "strong requirements",
                        ]
                    ),
                }
            ),
            supervised_keys=None,
            homepage=_HOMEPAGE,
            license=_LICENSE,
            citation=_CITATION,
        )

    def _split_generators(self, dl_manager):
        """Returns SplitGenerators."""

        train_path = dl_manager.download_and_extract(_TRAIN_DOWNLOAD_URL)
        return [
            datasets.SplitGenerator(name=datasets.Split.TRAIN, gen_kwargs={"filepath": train_path}),
        ]

    def _generate_examples(self, filepath):
        """Generate KorSAE examples"""

        with open(filepath, encoding="utf-8") as csv_file:
            data = csv.reader(csv_file, delimiter="\t")
            for id_, row in enumerate(data):
                intent_pair1, intent_pair2, label = row
                yield id_, {"intent_pair1": intent_pair1, "intent_pair2": intent_pair2, "label": int(label)}

In [4]:
!gdown /content/sae4k_v2.txt #파일 다운

Failed to retrieve file url:

	Cannot retrieve the public link of the file. You may need to change
	the permission to 'Anyone with the link', or have had many accesses.

You may still be able to access the file from the browser:

	https://drive.google.com/uc?id=/content/sae4k_v2.txt

but Gdown can't. Please check connections and permissions.


# TF-IDF 단어 축약


In [8]:
# 파일 내용 열고 읽기
with open("/content/sae4k_v2.txt", "r", encoding="utf-8") as file:
    content = file.read()

# 파일 보기
content_preview = content[:]
content_preview


'2\t이번 주에 기온변화가 가장 큰 요일을 알려줘\t이번 주 기온변화 가장 큰 요일\n0\t공기청정기 켜져있니\t공기청정기 켜졌는지\n0\t오늘 오후에 수영대회가 있니\t오늘 오후 수영대회 여부\n3\t가급적 아이리버 엠피쓰리는 사지 않도록 합시다 \t아이리버 엠피쓰리 사지 않기\n3\t전체 메일을 쓸 때 민감한 내용은 쓰지마\t민감한 내용 전체메일 보내지 않기\n2\t이번주에 눈 언제 내리니\t이번주 눈 내리는 날\n2\t네이버 메일 이용 시 사용할 수 있는 클라우드 서비스가 뭐야 \t네이버 메일과 연동된 클라우드 서비스\n2\t혀를 깨물면 왜 죽니 \t혀를 깨물면 죽는 이유\n4\t화장실 환풍기 틀어줄래\t화장실 환풍기 틀기\n2\t내일 오전 울릉도에 바람이 얼마나 부는지 알려줘\t내일 오전 울릉도 풍량\n2\t동아대 근처 많이 가는 밥집 어떻게 가는가\t동아대 근처 많이 가는 밥집 가는 방법\n2\t소나기가 몇 시에 내리기 시작하니\t오늘 소나기 내리기 시작하는 시간\n0\t오늘 일정에 저녁약속이 있니\t오늘 일정 저녁약속 여부\n1\t페이스북이랑 인스타그램 중 이메일로 로그인하는게 뭐지 \t페이스북과 인스타그램 중 메일 주소로 로그인하는 서비스\n4\t메일함에서 학회 검색해줘\t메일함에서 학회 검색하기\n3\t운동 스케쥴 미루면 한도 끝도 없으니까 미루지 마 \t운동 스케쥴 미루지 않기\n2\t가장 인기 많은 라떼는 어느 것입니까 \t가장 인기 많은 라떼\n4\t다음 달 육일 오전 아홉시에 수강신청 일정 추가해줄수있니\t다음달 육일 오전 아홉시 수강신청 일정 추가하기\n2\t요리 레시피 요청하고 싶을 때는 어떻게 말해 \t요리 레시피 요청하는 방법\n0\t오늘 오후 비가오는지 확인해알려주겠니\t오늘 오후 비 오는지\n2\t집합론에서 다루는 수 체계의 종류는 뭐가 있죠 \t집합론에서 배우는 수 체계의 종류\n4\t투자할 때는 항상 최악을 생각하고 투자해 덜 손해봐\t항상 최악을 생각하고 투자하기\n2\t언론에서 홍콩 운동에 대해서 진행 상황 말해줬어 \

In [9]:
!pip install konlpy

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.4/19.4 MB 33.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 488.6/488.6 kB 45.4 MB/s eta 0:00:00


In [10]:
from konlpy.tag import Okt
from sklearn.feature_extraction.text import TfidfVectorizer

okt = Okt()

def extract_important_words(sentence: str, n=3) -> str:
    """
    Okt와 TF-IDF를 사용하여 문장에서 n개의 가장 중요한 단어를 추출합니다.
    """
    # Okt를 사용하여 문장 토큰화
    words = okt.nouns(sentence)  # 간단하게 하기 위해 명사만 추출합니다.

    # 단어가 n개 이하이면 모든 단어를 반환
    if len(words) <= n:
        return ' '.join(words)

    # 그렇지 않으면 각 단어의 TF-IDF 점수를 계산하고 상위 n개의 단어를 선택
    vectorizer = TfidfVectorizer().fit(words)
    word_tfidf_scores = vectorizer.transform(words).sum(axis=0).tolist()[0]

    sorted_words = [word for _, word in sorted(zip(word_tfidf_scores, words), reverse=True)]

    return ' '.join(sorted_words[:n])

# 함수 테스트
sample_sentence = "지금 너희 집으로 가고있는데 몇시쯤 도착해?"
important_words = extract_important_words(sample_sentence, 3)
print(important_words)


집 지금 너희


# Lstm모델을 이용한 감성분석


In [11]:
import pandas as pd
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from sklearn.model_selection import train_test_split

# 1. 데이터 로딩
def load_and_parse_data(filepath):
    data = {
        "label": [],
        "intent_pair1": [],
        "intent_pair2": []
    }

    with open(filepath, "r", encoding="utf-8") as file:
        for line in file:
            parts = line.strip().split("\t")
            data["label"].append(int(parts[0]))
            data["intent_pair1"].append(parts[1])
            data["intent_pair2"].append(parts[2])

    return pd.DataFrame(data)

df = load_and_parse_data("/content/sae4k_v2.txt")

# 2. 데이터 전처리
MAX_WORDS = 10000 # 고려할 최대 단어수 = 최빈값 10000개만 고려하기

tokenizer = Tokenizer(num_words=MAX_WORDS, oov_token='<OOV>') #케라스 제공 텍스트 토큰화, ov_token='<OOV>' =  본적없는 단어 나올시 대체(일반화)
tokenizer.fit_on_texts(df['intent_pair1']) #텍스트 토큰화 진행

sequences = tokenizer.texts_to_sequences(df['intent_pair1']) # 텍스트 데이터를 숫자 시퀀스로 변환
X = pad_sequences(sequences)
y = to_categorical(df['label'])

X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.3, random_state=42) #분할 비율 (70% 학습, 15% 검증, 15% 테스트)더 많은 데이터 80 10 10도 가능
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)

# 3. 모델 구성 및 학습
model = tf.keras.Sequential([
    tf.keras.layers.Embedding(MAX_WORDS, 128, input_length=X.shape[1]), #Embedding 층: 주어진 단어의 정수 인덱스를 벡터 형태로 변환
    tf.keras.layers.LSTM(128, return_sequences=True), #LSTM 층 (128 뉴런) True 옵션을 사용해서 다음층으로 전달
    tf.keras.layers.LSTM(64), #추가처리 64층
    tf.keras.layers.Dense(64, activation='relu'), #Dense 층 (64 뉴런): 히든 레이어로, ReLU 활성화 함수를 사용
    tf.keras.layers.Dropout(0.5), # Dropout 층: 과적합을 방지하기 위해 사용됩
    tf.keras.layers.Dense(len(df['label'].unique()), activation='softmax') # Dense 층: 최종 출력 층으로, 다중 분류를 위한 softmax 활성화 함수사용
])

model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
history = model.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_val, y_val))


Epoch 1/10
1113/1113 [==============================] - 113s 95ms/step - loss: 0.7109 - accuracy: 0.7468 - val_loss: 0.3909 - val_accuracy: 0.8670
Epoch 2/10
1113/1113 [==============================] - 105s 94ms/step - loss: 0.2874 - accuracy: 0.9109 - val_loss: 0.3632 - val_accuracy: 0.8876
Epoch 3/10
1113/1113 [==============================] - 103s 93ms/step - loss: 0.1911 - accuracy: 0.9420 - val_loss: 0.3720 - val_accuracy: 0.8935
Epoch 4/10
1113/1113 [==============================] - 112s 101ms/step - loss: 0.1511 - accuracy: 0.9532 - val_loss: 0.3938 - val_accuracy: 0.8864
Epoch 5/10
1113/1113 [==============================] - 109s 98ms/step - loss: 0.1235 - accuracy: 0.9616 - val_loss: 0.4350 - val_accuracy: 0.8883
Epoch 6/10
1113/1113 [==============================] - 108s 97ms/step - loss: 0.1041 - accuracy: 0.9668 - val_loss: 0.4686 - val_accuracy: 0.8897
Epoch 7/10
1113/1113 [==============================] - 106s 95ms/step - loss: 0.0881 - accuracy: 0.9707 - val_loss: 

In [12]:
# 모델의 가중치 개수 계산
num_weights = sum([tf.size(w).numpy() for w in model.weights])

# 훈련 정확도를 가져오기
final_training_accuracy = history.history['accuracy'][-1]

num_weights, final_training_accuracy


(1465542, 0.9776028990745544)

In [13]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [14]:
loss, accuracy = model.evaluate(X_test, y_test) #테스트 데이터로 모델 성능평가
print(f"Test Loss: {loss:.4f}")
print(f"Test Accuracy: {accuracy:.4f}")


239/239 [==============================] - 6s 25ms/step - loss: 0.6157 - accuracy: 0.8980
Test Loss: 0.6157
Test Accuracy: 0.8980


In [17]:
# 새로운 데이터 넣어서 모델 평가해보기
# 레이블의 인덱스와 실제 레이블 값의 매핑 정보를 포함하는 한글 리스트를 생성
LABELS = ["예/아니오", "대체", "wh- 질문", "금지", "요구사항", "강한 요구사항"]

def predict_intent(sentence):
    # 토큰화 및 패딩
    sequence = tokenizer.texts_to_sequences([sentence])
    padded_sequence = pad_sequences(sequence, maxlen=X.shape[1])

    # 예측
    prediction = model.predict(padded_sequence)
    predicted_label = LABELS[prediction.argmax()]

    return predicted_label

# 예측 테스트
sentence = "진행해 주세요"
print(f"Predicted Intent: {predict_intent(sentence)}")


1/1 [==============================] - 0s 45ms/step
Predicted Intent: 요구사항


In [ ]:
# 강한 요구사항을 출력 어려움

In [ ]:
from google.colab import drive
drive.mount('/content/drive')